In [1]:
import geopandas as gpd
import pandas as pd
import re
from fuzzywuzzy import fuzz
import string


In [2]:


adressen = gpd.read_file("C:\dev\ews\data\AV_MOpublic-_Gebaudeadressen_-OGD.gpkg", layer="AVZH_GEBAEUDEEINGANG_P")

mastersonden = gpd.read_file("C:\dev\ews\data\Erdwarmesonden_-OGD.gpkg", layer="GS_MASTERSONDEN_P")

gebäude = gpd.read_file("C:\dev\ews\data\AV_MOpublic-_Bodenbedeckung_-OGD.gpkg", layer="AVZH_BODENBEDECKUNG_F")

proj_gebäude = gpd.read_file("C:\dev\ews\data\AV_MOpublic-_Bodenbedeckung_-OGD.gpkg", layer="AVZH_BODENBEDECKUNG_PROJ_F")

gemeinden = gpd.read_file("C:\dev\ews\data\Gemeindegrenzen_-OGD.gpkg", layer="UP_GEMEINDEN_F")

liegeschaften = gpd.read_file("C:\dev\ews\data\AV_MOpublic-_Liegenschaften_-OGD.gpkg", layer="AVZH_LIEGENSCHAFTEN_F")

# create the final output dataframe
output = gpd.GeoDataFrame(columns=["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "DISTANCE", "VARIANTE", "geometry"])
output_spatial = gpd.GeoDataFrame(columns=["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "DISTANCE", "VARIANTE", "geometry"])


In [3]:
adressen.drop(columns=['OBJID','GUELTIGKEIT','POSX','POSY','HOEHENLAGE','GEBAEUDENAME','GWR_EDID','PLZ','ZUSATZZIFFERN','ORTSCHAFTSNAME','BEARBEITUNGSDATUM','BEWILLIGUNGSSTATUS','REFID_LOKALISATION','ISTOFFIZIELLEBEZEICHNUNG'], inplace=True)


#remove useless attributes
liegeschaften.drop(columns=['OBJID','NBIDENT','NUMMER','VOLLSTAENDIGKEIT','FLAECHENMASS','BFSNR','BEARBEITUNGSDATUM','SHAPE_AREA','SHAPE_LEN'], inplace=True)


#filter only gebäude, remove useless attributes
gebäude = gebäude[(gebäude['ART'] == 'Gebäude')]
proj_gebäude = proj_gebäude[proj_gebäude['ARTZHID'].isin([0, 1, 2, 3, 4, 5, 6, 7])]

gebäude.drop(columns=['OBJID','QUALITAET','ART','BEARBEITUNGSDATUM','ARTCHID','ARTZHID','GVZNUMMER','SHAPE_AREA','SHAPE_LEN'], inplace=True)
proj_gebäude.drop(columns=['OBJID','QUALITAET','ART','BEARBEITUNGSDATUM','ARTCHID','ARTZHID','GVZNUMMER','SHAPE_AREA','SHAPE_LEN','BEWILLIGUNGSSTATUS'], inplace=True)

#remove useless attributes
mastersonden.drop(columns=['X_KOORD','Y_KOORD','SONDENTIEFE','KATASTERNUMMER','GESAMTSONDENANZAHL','STATUS','ERFASSUNG','GUELTIGKEIT','BOHRPROFIL','WAERMEENTNAHME','WAERMEEINTRAG'], inplace=True)


In [4]:
korregiert = pd.read_excel(r"C:\Users\BAA1964\Downloads\2025-05_Korrigierte Sonden-Standorte.xlsx")
korregiert_sub = korregiert[['GBS','StandortSonde korrigiert']]


In [5]:



merged = mastersonden.merge(korregiert_sub, left_on='GBS_ID', right_on='GBS', how='left')

# Overwrite address with corrected_address where it's not null
merged['STANDORT'] = merged['StandortSonde korrigiert'].combine_first(merged['STANDORT'])

# If you no longer need the corrected_address column:
merged.drop(columns='StandortSonde korrigiert', inplace=True)

#patial join with gemeinden
sonden_bfs = merged.sjoin(gemeinden[['BFS','geometry']], how='inner', predicate='intersects')
sonden_bfs.drop(columns=['index_right'], inplace=True)


In [6]:
# #read uncut sonden location

# ews_sonden = gpd.read_file("EWS_Bewilligungen komplett Ende 2024.xlsx", encoding="utf-8")
# ews_sonden = ews_sonden[ews_sonden['Check Textlänge'] == 'Cut']

# # take the standort from the ews_sonden if it is not empty
# mastersonden['STANDORT'] = mastersonden['GBS_ID'].map(ews_sonden.set_index('gbs_id')['Adresse EWS']).fillna(mastersonden['STANDORT'])


In [7]:
proj_gebäude_adressen = proj_gebäude.sjoin(adressen, how='inner', predicate='intersects')
proj_gebäude_adressen['GWR_EGID'] = proj_gebäude_adressen['GWR_EGID_left'].fillna(proj_gebäude_adressen['GWR_EGID_right'])
proj_gebäude_adressen = proj_gebäude_adressen[~proj_gebäude_adressen['HAUSNUMMER'].astype(str).str.contains('\.')]
proj_gebäude_adressen['ADRESSE'] = proj_gebäude_adressen['LOKALISATIONSNAME'] + ' ' + proj_gebäude_adressen['HAUSNUMMER']

# Split the dataset
proj_non_empty_gwr = proj_gebäude_adressen[proj_gebäude_adressen['GWR_EGID'].notna() & (proj_gebäude_adressen['GWR_EGID'] != '')]
proj_empty_gwr = proj_gebäude_adressen[proj_gebäude_adressen['GWR_EGID'].isna() | (proj_gebäude_adressen['GWR_EGID'] == '')]

# Group geometry (pick first geometry)
geometry_map = proj_non_empty_gwr.groupby('GWR_EGID')['geometry'].first().reset_index()

# Group other attributes
grouped_attributes = proj_non_empty_gwr.drop(columns='geometry').groupby('GWR_EGID').agg(
    lambda x: ', '.join(map(str, set(x)))
).reset_index()

# Merge geometry back
grouped_non_empty_gwr = grouped_attributes.merge(geometry_map, on='GWR_EGID', how='left')

# Convert to GeoDataFrame
grouped_non_empty_gwr = gpd.GeoDataFrame(grouped_non_empty_gwr, geometry='geometry', crs=proj_gebäude_adressen.crs)

# Recombine with rows that had empty GWR_EGID
grouped_proj_gebäude_adressen = pd.concat([grouped_non_empty_gwr, proj_empty_gwr], ignore_index=True)

# Optional: drop unnecessary columns
if 'index_right' in grouped_proj_gebäude_adressen.columns:
    grouped_proj_gebäude_adressen.drop(columns=['index_right'], inplace=True)

In [8]:
gebäude_adressen = gebäude.sjoin(adressen, how='inner', predicate='intersects')
gebäude_adressen['GWR_EGID'] = gebäude_adressen['GWR_EGID_left'].fillna(gebäude_adressen['GWR_EGID_right'])
gebäude_adressen = gebäude_adressen[~gebäude_adressen['HAUSNUMMER'].astype(str).str.contains('\.')]
gebäude_adressen['ADRESSE'] = gebäude_adressen['LOKALISATIONSNAME'] + ' ' + gebäude_adressen['HAUSNUMMER']

# Split the dataset
non_empty_gwr = gebäude_adressen[gebäude_adressen['GWR_EGID'].notna() & (gebäude_adressen['GWR_EGID'] != '')]
empty_gwr = gebäude_adressen[gebäude_adressen['GWR_EGID'].isna() | (gebäude_adressen['GWR_EGID'] == '')]

# Group geometry (pick first geometry)
geometry_map = non_empty_gwr.groupby('GWR_EGID')['geometry'].first().reset_index()

# Group other attributes
grouped_attributes = non_empty_gwr.drop(columns='geometry').groupby('GWR_EGID').agg(
    lambda x: ', '.join(map(str, set(x)))
).reset_index()

# Merge geometry back
grouped_non_empty_gwr = grouped_attributes.merge(geometry_map, on='GWR_EGID', how='left')

# Convert to GeoDataFrame
grouped_non_empty_gwr = gpd.GeoDataFrame(grouped_non_empty_gwr, geometry='geometry', crs=gebäude_adressen.crs)

# Recombine with rows that had empty GWR_EGID
grouped_gebäude_adressen = pd.concat([grouped_non_empty_gwr, empty_gwr], ignore_index=True)

# Optional: drop unnecessary columns
if 'index_right' in grouped_gebäude_adressen.columns:
    grouped_gebäude_adressen.drop(columns=['index_right'], inplace=True)

In [9]:
#spatial join with gebäude
proj_gebäude_sonden = sonden_bfs.sjoin(grouped_proj_gebäude_adressen, how='inner', predicate='intersects')
# proj_gebäude_sonden = proj_gebäude_sonden[proj_gebäude_sonden['ARTZH'] == "Gebäude Wohnen"]

#define variante
proj_gebäude_sonden['VARIANTE'] = 'Projektiere Gebäude Spatial Join'

#add the adressen_sonden to the output dataframe
output_spatial = gpd.GeoDataFrame(pd.concat([output_spatial, proj_gebäude_sonden[["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "VARIANTE", "geometry"]]], ignore_index=True))

not_proj_geb_joined = sonden_bfs[~sonden_bfs['GBS_ID'].isin(output_spatial['GBS_ID'])]

In [10]:
#spatial join with gebäude
gebäude_sonden = not_proj_geb_joined.sjoin(grouped_gebäude_adressen, how='inner', predicate='intersects')
gebäude_sonden = gebäude_sonden[gebäude_sonden['ARTZH'] == "Gebäude Wohnen"]

#define variante
gebäude_sonden['VARIANTE'] = 'Gebäude Spatial Join'

#add the adressen_sonden to the output dataframe
output_spatial = gpd.GeoDataFrame(pd.concat([output_spatial, gebäude_sonden[["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "VARIANTE", "geometry"]]], ignore_index=True))

not_geb_joined = not_proj_geb_joined[~not_proj_geb_joined['GBS_ID'].isin(output['GBS_ID'])]

In [11]:
sonden_bfs

GBS_ID              STANDORT                         geometry  GBS  \
0      m 00-01428   Im Hintereichen 1+3  POINT (2670319.993 1261873.996)  NaN   
1      m 00-12167          Im Gupfen 18  POINT (2670354.992 1261711.995)  NaN   
2      m 00-01401         Gupfenstrasse  POINT (2670378.993 1261814.995)  NaN   
3      m 00-01188  Tannrietlistrasse 20  POINT (2670449.993 1261513.993)  NaN   
4      m 00-01178  Tannrietlistrasse 13  POINT (2670484.993 1261527.992)  NaN   
...           ...                   ...                              ...  ...   
36344  h 00-11058              Gfell 18  POINT (2712870.819 1248973.824)  NaN   
36345  f 00-12106          Im Brand 14a  POINT (2713283.799 1236150.792)  NaN   
36346  f 00-10938           Risigrund 1  POINT (2713694.782 1245573.802)  NaN   
36347  f 00-10937             Chlital 2  POINT (2714413.778 1245376.801)  NaN   
36348  f 00-01296             Fuchsloch  POINT (2714595.776 1245489.803)  NaN   

       BFS  
0       91  
1       91  
2       91  
3       91  
4       91  
...    ...  
36344  297  
36345  120  
36346  114  
36347  114  
36348  114  

[36349 rows x 5 columns]

In [12]:
# creat complete adresse, remove useless attributes
adressen['ADRESSE'] = adressen['LOKALISATIONSNAME'] + ' ' + adressen['HAUSNUMMER']

adressen.drop(columns=['HAUSNUMMER','LOKALISATIONSNAME'], inplace=True)

#unify the address format
adressen['ADRESSE_conc'] = adressen['ADRESSE'].str.lower().str.replace(' ', '')
sonden_bfs['STANDORT_conc'] = sonden_bfs['STANDORT'].str.lower().str.replace(' ', '')

# merge sonden with adressen
adressen_sonden = adressen.merge(sonden_bfs[['STANDORT_conc','GBS_ID','STANDORT','BFS']], how='inner', left_on=['ADRESSE_conc','BFSNR'], right_on=['STANDORT_conc','BFS'])

In [13]:
# Initialize a list to store indices of rows to delete
to_delete = []

# Record the initial number of entries
initial_count = len(adressen_sonden)

# Loop through `adressen_sonden` and check distance to matching entry in `mastersonden`
for idx, adresse in adressen_sonden.iterrows():
    # Find the matching entry in `mastersonden` by GBS_ID
    matching_sonde = mastersonden[mastersonden['GBS_ID'] == adresse['GBS_ID']]
    
    # Skip if no matching GBS_ID found
    if matching_sonde.empty:
        print(f"GBS_ID {adresse['GBS_ID']} not found in mastersonden")
        continue

    # Get the geometry safely
    adresse_geom = adresse.geometry
    master_geom = matching_sonde.geometry.iloc[0]

    # Check for missing geometry
    if adresse_geom is None or master_geom is None:
        print(f"GBS_ID {adresse['GBS_ID']} has missing geometry.")
        continue

    # Calculate distance
    distance = adresse_geom.distance(master_geom)
    print(f"GBS_ID {adresse['GBS_ID']}: Distance = {distance:.2f} meters")

    # Store the distance
    adressen_sonden.at[idx, 'DISTANCE'] = distance

    # Flag for deletion if distance > 1000 meters
    if distance > 500:
        print(f"GBS_ID {adresse['GBS_ID']}: Failed (Distance > 1 km), marking for deletion.")
        to_delete.append(idx)

# Drop the flagged rows
adressen_sonden = adressen_sonden.drop(to_delete)

# Record final count
final_count = len(adressen_sonden)
deleted_count = initial_count - final_count

# Report
print(f"Remaining entries in adressen_sonden: {final_count}")
print(f"Entries deleted: {deleted_count}")


GBS_ID m 00-11863: Distance = 10.65 meters
GBS_ID m 00-11025: Distance = 9.54 meters
GBS_ID m 00-10512: Distance = 4.29 meters
GBS_ID m 09-10004: Distance = 10.14 meters
GBS_ID m 00-01184: Distance = 4.47 meters
GBS_ID m 00-01186: Distance = 5.09 meters
GBS_ID m 00-01189: Distance = 4.47 meters
GBS_ID m 00-01173: Distance = 4.68 meters
GBS_ID m 00-11375: Distance = 25.64 meters
GBS_ID m 00-11249: Distance = 18.77 meters
GBS_ID n 00-10371: Distance = 20.86 meters
GBS_ID m 00-11174: Distance = 1.13 meters
GBS_ID m 00-11176: Distance = 1.18 meters
GBS_ID n 00-10573: Distance = 9.74 meters
GBS_ID n 00-02040: Distance = 7.05 meters
GBS_ID m 00-11209: Distance = 4.14 meters
GBS_ID m 00-11212: Distance = 3.32 meters
GBS_ID m 00-11991: Distance = 5.89 meters
GBS_ID n 00-10127: Distance = 5.95 meters
GBS_ID m 00-10795: Distance = 5.42 meters
GBS_ID m 00-11225: Distance = 4.96 meters
GBS_ID m 00-11232: Distance = 22.11 meters
GBS_ID m 00-11229: Distance = 6.49 meters
GBS_ID m 00-11411: Distance 

In [14]:
adressen_sonden

GWR_EGID  BFSNR                         geometry  \
0          33318.0     91  POINT (2669651.428 1261182.065)   
1      201021396.0     91  POINT (2670281.628 1261692.514)   
2          33302.0     91  POINT (2670436.196 1261619.867)   
3          33072.0     91  POINT (2670418.084 1262631.923)   
4        3017098.0     91  POINT (2670527.142 1261480.912)   
...            ...    ...                              ...   
25527  210220128.0    120  POINT (2712401.212 1237460.166)   
25528      49312.0    120  POINT (2712528.619 1236156.154)   
25529    3018815.0    120  POINT (2712884.675 1235913.587)   
25530      41160.0    114  POINT (2712909.118 1245806.952)   
25531      41185.0    114  POINT (2713678.278 1245585.579)   

                    ADRESSE         ADRESSE_conc        STANDORT_conc  \
0            Surbengraben 1        surbengraben1        surbengraben1   
1             Mustergass 10         mustergass10         mustergass10   
2       Tannrietlistrasse 6   tannrietlistrasse6   tannrietlistrasse6   
3           Im Binzacher 20        imbinzacher20        imbinzacher20   
4      Tannrietlistrasse 25  tannrietlistrasse25  tannrietlistrasse25   
...                     ...                  ...                  ...   
25527  Sanatoriumstrasse 60  sanatoriumstrasse60  sanatoriumstrasse60   
25528    Hofacherstrasse 12    hofacherstrasse12    hofacherstrasse12   
25529    Mürtschenstrasse 2    mürtschenstrasse2    mürtschenstrasse2   
25530     Bahnhofstrasse 17     bahnhofstrasse17     bahnhofstrasse17   
25531           Risigrund 1           risigrund1           risigrund1   

           GBS_ID              STANDORT  BFS   DISTANCE  
0      m 00-11863        Surbengraben 1   91  10.645448  
1      m 00-11025         Mustergass 10   91   9.540223  
2      m 00-10512   Tannrietlistrasse 6   91   4.292911  
3      m 09-10004       Im Binzacher 20   91  10.139733  
4      m 00-01184  Tannrietlistrasse 25   91   4.470414  
...           ...                   ...  ...        ...  
25527  f 00-11727  Sanatoriumstrasse 60  120   9.583516  
25528  f 00-11996    Hofacherstrasse 12  120  12.394144  
25529  f 00-11932    Mürtschenstrasse 2  120  22.373868  
25530  f 01-10003     Bahnhofstrasse 17  114  11.864250  
25531  f 00-10938           Risigrund 1  114  20.275102  

[25444 rows x 10 columns]

In [15]:
#add the adressen_sonden to the output dataframe
adressen_sonden['VARIANTE'] = "Single Adress Join"

output = gpd.GeoDataFrame(pd.concat([output, adressen_sonden[["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "DISTANCE", "VARIANTE", "geometry"]]], ignore_index=True))

not_adress_joined = sonden_bfs[~sonden_bfs['GBS_ID'].isin(output['GBS_ID'])]

In [16]:
output

STANDORT               ADRESSE      GBS_ID     GWR_EGID  \
0            Surbengraben 1        Surbengraben 1  m 00-11863      33318.0   
1             Mustergass 10         Mustergass 10  m 00-11025  201021396.0   
2       Tannrietlistrasse 6   Tannrietlistrasse 6  m 00-10512      33302.0   
3           Im Binzacher 20       Im Binzacher 20  m 09-10004      33072.0   
4      Tannrietlistrasse 25  Tannrietlistrasse 25  m 00-01184    3017098.0   
...                     ...                   ...         ...          ...   
25439  Sanatoriumstrasse 60  Sanatoriumstrasse 60  f 00-11727  210220128.0   
25440    Hofacherstrasse 12    Hofacherstrasse 12  f 00-11996      49312.0   
25441    Mürtschenstrasse 2    Mürtschenstrasse 2  f 00-11932    3018815.0   
25442     Bahnhofstrasse 17     Bahnhofstrasse 17  f 01-10003      41160.0   
25443           Risigrund 1           Risigrund 1  f 00-10938      41185.0   

        DISTANCE            VARIANTE                         geometry  
0      10.645448  Single Adress Join  POINT (2669651.428 1261182.065)  
1       9.540223  Single Adress Join  POINT (2670281.628 1261692.514)  
2       4.292911  Single Adress Join  POINT (2670436.196 1261619.867)  
3      10.139733  Single Adress Join  POINT (2670418.084 1262631.923)  
4       4.470414  Single Adress Join  POINT (2670527.142 1261480.912)  
...          ...                 ...                              ...  
25439   9.583516  Single Adress Join  POINT (2712401.212 1237460.166)  
25440  12.394144  Single Adress Join  POINT (2712528.619 1236156.154)  
25441  22.373868  Single Adress Join  POINT (2712884.675 1235913.587)  
25442  11.864250  Single Adress Join  POINT (2712909.118 1245806.952)  
25443  20.275102  Single Adress Join  POINT (2713678.278 1245585.579)  

[25444 rows x 7 columns]

In [17]:
def normalize_delimiters(text):
    # Replace /, +, &, ; with comma
    text = re.sub(r'[\/\+&;]', ',', text)

    # Replace whole words "und" or "sowie" with comma (using word boundaries)
    text = re.sub(r'\b(und|sowie|uns)\b', ',', text, flags=re.IGNORECASE)

    return text


not_adress_joined['STANDORT'] = not_adress_joined['STANDORT'].apply(normalize_delimiters)

c:\Users\BAA1964\AppData\Local\ESRI\conda\envs\scratch\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [18]:
# function to split the STANDORT into the street names
def split_address(text):
    
    # Handle non-string or missing input
    if not isinstance(text, str):
        return [text]
    
    # Define the updated pattern to handle street names and house numbers
    pattern = r'^\s?[a-zA-Zäöüß.\-]{2,}[a-zA-Zäöüß.\-\s]{1}[a-zA-Zäöüß.\-\s]{2,}\d+'  # Match street names followed by at least one digit
    
    # Define the delimiter
    delimiters = ['und', ',', 'sowie','\r\n']
    

    for delimiter in delimiters:
        # Loop to progressively split at each 'und'
        c = 1
        while delimiter in text:
            # Split at the c-th occurrence of 'und'
            parts = text.split(delimiter, c)  # Split at the c-th 'und'
            print(parts)
            if c != 1:
                parts = [delimiter.join(parts[:c])] + parts[c:]
                print(f"Corrected parts after joining: {parts}")

            print(f"Splitting at {c}-th occurrence of '{delimiter}' -> Parts: {parts}")

            # After splitting, check if all parts are valid
            if all(re.search(pattern, part.strip()) for part in parts):
                print(f"Valid parts found at {c}-th occurrence of '{delimiter}': {parts}")
                return parts  # Return valid parts if all match the pattern
            
            if delimiter not in parts[1]:
                break
            # If parts are not valid, rebuild the text and move to the next occurrence of 'und'
            c += 1  # Move on to the next occurrence to split
        
    # If no valid parts found after all splits, return the original text
    print("No valid parts found based on the pattern.")
    return [text]


In [19]:
# apply the split_address function until all addresses are split

initial_count = len(not_adress_joined)
loop = 0

while True:
    # Apply the split_address function to the 'STANDORT' column and create a new column for each loop
    if loop == 0:
        not_adress_joined['split_address_0'] = not_adress_joined['STANDORT'].apply(split_address)
    else:
        not_adress_joined['split_address_' + str(loop)] = not_adress_joined['split_address_' + str(loop-1)].apply(split_address)
    
    # Explode the DataFrame based on the current split_address column
    exploded_df = not_adress_joined.explode('split_address_' + str(loop))

    # Check if any new rows were created
    if len(exploded_df) == len(not_adress_joined):
        break  # Exit the loop if no new rows were created

    # Update not_adress_joined to the exploded DataFrame for the next iteration
    not_adress_joined = exploded_df.copy()

    # Increment the loop counter for the next iteration
    loop += 1


['Im Hintereichen 1', '3']
Splitting at 1-th occurrence of ',' -> Parts: ['Im Hintereichen 1', '3']
No valid parts found based on the pattern.
No valid parts found based on the pattern.
No valid parts found based on the pattern.
No valid parts found based on the pattern.
No valid parts found based on the pattern.
['Brunnenweg 1', ' 3, 5, 7, 9, 11']
Splitting at 1-th occurrence of ',' -> Parts: ['Brunnenweg 1', ' 3, 5, 7, 9, 11']
['Brunnenweg 1', ' 3', ' 5, 7, 9, 11']
Corrected parts after joining: ['Brunnenweg 1, 3', ' 5, 7, 9, 11']
Splitting at 2-th occurrence of ',' -> Parts: ['Brunnenweg 1, 3', ' 5, 7, 9, 11']
['Brunnenweg 1', ' 3', ' 5', ' 7, 9, 11']
Corrected parts after joining: ['Brunnenweg 1, 3, 5', ' 7, 9, 11']
Splitting at 3-th occurrence of ',' -> Parts: ['Brunnenweg 1, 3, 5', ' 7, 9, 11']
['Brunnenweg 1', ' 3', ' 5', ' 7', ' 9, 11']
Corrected parts after joining: ['Brunnenweg 1, 3, 5, 7', ' 9, 11']
Splitting at 4-th occurrence of ',' -> Parts: ['Brunnenweg 1, 3, 5, 7', ' 9,

c:\Users\BAA1964\AppData\Local\ESRI\conda\envs\scratch\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


['Im Hintereichen 1', '3']
Splitting at 1-th occurrence of ',' -> Parts: ['Im Hintereichen 1', '3']
No valid parts found based on the pattern.
No valid parts found based on the pattern.
No valid parts found based on the pattern.
No valid parts found based on the pattern.
No valid parts found based on the pattern.
['Brunnenweg 1', ' 3, 5, 7, 9, 11']
Splitting at 1-th occurrence of ',' -> Parts: ['Brunnenweg 1', ' 3, 5, 7, 9, 11']
['Brunnenweg 1', ' 3', ' 5, 7, 9, 11']
Corrected parts after joining: ['Brunnenweg 1, 3', ' 5, 7, 9, 11']
Splitting at 2-th occurrence of ',' -> Parts: ['Brunnenweg 1, 3', ' 5, 7, 9, 11']
['Brunnenweg 1', ' 3', ' 5', ' 7, 9, 11']
Corrected parts after joining: ['Brunnenweg 1, 3, 5', ' 7, 9, 11']
Splitting at 3-th occurrence of ',' -> Parts: ['Brunnenweg 1, 3, 5', ' 7, 9, 11']
['Brunnenweg 1', ' 3', ' 5', ' 7', ' 9, 11']
Corrected parts after joining: ['Brunnenweg 1, 3, 5, 7', ' 9, 11']
Splitting at 4-th occurrence of ',' -> Parts: ['Brunnenweg 1, 3, 5, 7', ' 9,

In [20]:
def process_letter_ranges(address):
    # Match pattern like: "dorfstrasse 51 a-i, 55 a+n, 57 a-m"
    street_match = re.match(r'([^\d]+)(\d.*)', address)

    if street_match:
        street_name = street_match.group(1).strip()
        rest = street_match.group(2).strip()

        address_parts = rest.split(',')

        result = []

        for part in address_parts:
            part = part.strip()

            # Match range like '51 a-i'
            range_match = re.match(r'(\d+)\s*([a-z])\s*-\s*([a-z])', part)
            if range_match:
                base_number = range_match.group(1)
                start_letter = range_match.group(2)
                end_letter = range_match.group(3)

                addresses = [
                    f"{street_name} {base_number}{chr(letter)}"
                    for letter in range(ord(start_letter), ord(end_letter) + 1)
                ]
                result.extend(addresses)
                continue

            # Match '12 a+b' or '12 a und b'
            plus_or_und_match = re.match(r'(\d+)\s*([a-z])\s*(\+|und)\s*([a-z])', part)
            if plus_or_und_match:
                base_number = plus_or_und_match.group(1)
                letter1 = plus_or_und_match.group(2)
                letter2 = plus_or_und_match.group(4)

                result.append(f"{street_name} {base_number}{letter1}")
                result.append(f"{street_name} {base_number}{letter2}")
                continue

            # No special pattern, just append as-is
            result.append(f"{street_name} {part.replace(' ', '')}")

        return result

    return [address]  # No match found, return the original address

def process_address(address):
    # Match the street name and the number part
    match = re.match(r'([^\d]+)(\d.*)', address)
    
    if match:
        street_name = match.group(1).strip()
        rest = match.group(2).strip()

        # Special case: something like 9-13a
        range_with_suffix_match = re.match(r'(\d+)\s*-\s*(\d+)([a-z]?)$', rest)
        if range_with_suffix_match:
            start = int(range_with_suffix_match.group(1))
            end = int(range_with_suffix_match.group(2))
            suffix = range_with_suffix_match.group(3)

            # Generate every second number
            result = []
            for i in range(start, end + 1, 2):
                if i == end and suffix:
                    result.append(f"{street_name} {i}{suffix}")
                else:
                    result.append(f"{street_name} {i}")
            return result

        # Handling 'bis' and '-' for plain numeric ranges
        if 'bis' in rest or '-' in rest:
            parts = re.split(r'[\sbis,-]+', rest)
            if len(parts) == 2 and parts[0].isdigit() and parts[1].isdigit():
                start = int(parts[0])
                end = int(parts[1])

                step = 2 if (start % 2 == end % 2) else 1
                return [f"{street_name} {i}" for i in range(start, end + 1, step)]

        # Split on known delimiters
        elif any(sep in rest for sep in ['und', ',']):
            parts = re.split(r'[,und]+', rest)
            return [f"{street_name} {part.strip()}" for part in parts]

        # No special case detected
        return [address]

    return [address]

In [21]:
# apply the proccesing functions until all addresses are processed

loop = 0

while True:
    # Store the initial count to compare later
    initial_count = len(exploded_df)

    # Apply the process_address function to the appropriate column in the DataFrame
    if loop == 0:
        exploded_df['clean_address_0'] = exploded_df['split_address_1'].str.lower().apply(process_address)
    else:
        exploded_df['clean_address_' + str(loop)] = exploded_df['clean_address_processed_' + str(loop-1)].apply(process_address)

    # Explode the DataFrame based on the current clean_address column
    exploded_df = exploded_df.explode('clean_address_' + str(loop)).fillna('')

    # Apply the process_letter_ranges function to the appropriate clean_address column
    if loop == 0:
        exploded_df['clean_address_processed_0'] = exploded_df['clean_address_0'].apply(process_letter_ranges)
    else:
        exploded_df['clean_address_processed_' + str(loop)] = exploded_df['clean_address_' + str(loop - 1)].apply(process_letter_ranges)

    # Explode the DataFrame based on the processed clean_address column
    exploded_df = exploded_df.explode('clean_address_processed_' + str(loop)).fillna('')

    # Check if any new rows were created by comparing the length of exploded_df
    if len(exploded_df) == initial_count:
        break  # Exit the loop if no new rows were created (i.e., no change)

    # Increment the loop counter for the next iteration
    loop += 1

In [22]:
#return true if the address has a number
def has_number(address):
    if isinstance(address, str):  # Ensure that the address is a string
        return bool(re.search(r'\d', address))  # Check if there is any digit
    return False  # Return False if the address is not a string (e.g., NaN or float)



# Remove duplicates based on the processed address column
exploded_df = exploded_df.drop_duplicates(subset=['clean_address_processed_3', 'GBS_ID'])

# Filter out rows where the processed address contains a number
processed_address = exploded_df[exploded_df['clean_address_processed_3'].apply(has_number)]

In [23]:
# Filter out rows where the processed address does not contain "haus" in the addres
def not_haus_in_adress(adressen):
    haus_pattern = r'\bhaus\b'

    re.search(haus_pattern, adressen, re.IGNORECASE)
    if re.search(haus_pattern, adressen, re.IGNORECASE):
        return False
    else:
        return True
    
# Filter out rows where the processed address contains "haus" in the address
processed_address = processed_address[processed_address['clean_address_processed_3'].apply(not_haus_in_adress)]

In [24]:
# unify the address format
processed_address['final_address'] = processed_address['clean_address_processed_3'].str.replace(' ', '').str.lower()

# merge the processed address with adressen
processed_address_sonden = adressen.merge(processed_address, how='inner', left_on=['ADRESSE_conc','BFSNR'], right_on=['final_address','BFS'])

In [25]:
processed_address_sonden = (
    processed_address_sonden
    .set_geometry('geometry_x')
    .rename(columns={'geometry_x': 'geometry'})
    .drop(columns=['geometry_y'], errors='ignore')
)


In [26]:
# Initialize a list to store indices of rows to delete
to_delete = []

# Record the initial number of entries
initial_count = len(processed_address_sonden)

# Loop through `processed_address_sonden` and check distance to matching entry in `mastersonden`
for idx, adresse in processed_address_sonden.iterrows():
    # Find the matching entry in `mastersonden` by GBS_ID
    matching_sonde = mastersonden[mastersonden['GBS_ID'] == adresse['GBS_ID']]
    
    # Skip if no matching GBS_ID found
    if matching_sonde.empty:
        print(f"GBS_ID {adresse['GBS_ID']} not found in mastersonden")
        continue

    # Get the geometry safely
    adresse_geom = adresse.geometry
    master_geom = matching_sonde.geometry.iloc[0]

    # Check for missing geometry
    if adresse_geom is None or master_geom is None:
        print(f"GBS_ID {adresse['GBS_ID']} has missing geometry.")
        continue

    # Calculate distance
    distance = adresse_geom.distance(master_geom)
    print(f"GBS_ID {adresse['GBS_ID']}: Distance = {distance:.2f} meters")

    # Store the distance
    processed_address_sonden.at[idx, 'DISTANCE'] = distance

    # Flag for deletion if distance > 1000 meters
    if distance > 500:
        print(f"GBS_ID {adresse['GBS_ID']}: Failed (Distance > 1 km), marking for deletion.")
        to_delete.append(idx)

# Drop the flagged rows
processed_address_sonden = processed_address_sonden.drop(to_delete)

# Record final count
final_count = len(processed_address_sonden)
deleted_count = initial_count - final_count

# Report
print(f"Remaining entries in processed_address_sonden: {final_count}")
print(f"Entries deleted: {deleted_count}")


GBS_ID m 00-11906: Distance = 49.22 meters
GBS_ID m 00-11906: Distance = 28.26 meters
GBS_ID m 00-11906: Distance = 35.92 meters
GBS_ID m 00-11906: Distance = 23.88 meters
GBS_ID m 00-11906: Distance = 25.45 meters
GBS_ID m 00-01273: Distance = 5.60 meters
GBS_ID m 00-11437: Distance = 14.36 meters
GBS_ID m 16-10013: Distance = 24.79 meters
GBS_ID n 01-10130: Distance = 5.13 meters
GBS_ID m 00-11857: Distance = 2.05 meters
GBS_ID m 00-11858: Distance = 1.20 meters
GBS_ID n 00-02121: Distance = 18.29 meters
GBS_ID m 00-10805: Distance = 0.82 meters
GBS_ID n 00-02075: Distance = 6.04 meters
GBS_ID n 00-02076: Distance = 6.37 meters
GBS_ID c 00-12546: Distance = 13.89 meters
GBS_ID c 01-10016: Distance = 17.95 meters
GBS_ID c 01-10049: Distance = 6.69 meters
GBS_ID c 01-10049: Distance = 1.88 meters
GBS_ID n 01-10116: Distance = 11.34 meters
GBS_ID n 01-10077: Distance = 26.93 meters
GBS_ID n 01-10077: Distance = 21.05 meters
GBS_ID n 01-10020: Distance = 22.39 meters
GBS_ID n 01-10023: D

In [27]:
processed_address_sonden['VARIANTE'] = 'Processed Adressen join'

output = gpd.GeoDataFrame(pd.concat([output, processed_address_sonden[["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "DISTANCE", "VARIANTE", "geometry"]]], ignore_index=True))

#filter the matched adressen_sonden out of the sonden_with_address_bfs
not_processed_adress_sonden_match = processed_address[~processed_address['GBS_ID'].isin(output['GBS_ID'])]

In [28]:
# Function to check if the digits in addresses match exactly, including the first non-digit after the digits if it exists
def check_digit_match(address1, address2):
    # Extract only digits from both addresses
    digits1 = ''.join(re.findall(r'\d', address1))
    digits2 = ''.join(re.findall(r'\d', address2))
    
    # Extract the first non-digit character after the digits, if any
    non_digit1 = re.search(r'\d(\D)', address1)  # Find the first non-digit after digits
    non_digit2 = re.search(r'\d(\D)', address2)  # Find the first non-digit after digits
    
    # Capture the first non-digit character after the digits or an empty string if not found
    non_digit1 = non_digit1.group(1) if non_digit1 else ''
    non_digit2 = non_digit2.group(1) if non_digit2 else ''
    
    # Compare both the digits and the first non-digit after the digits
    return digits1 + non_digit1 == digits2 + non_digit2  # Exact match for digits + first non-digit after digits

# Function to extract the street name and number separately
def extract_street_and_number(address):
    # Use regex to separate street name and number
    match = re.match(r"([^\d]+)(\d+[\w]*)", address.strip())
    if match:
        street_name = match.group(1).strip()
        number = match.group(2).strip()
        return street_name, number
    return address, ""  # In case there's no match, return whole address as street_name

# Function for fuzzy matching based on street name
def is_high_fuzzy_match(street1, street2, threshold=80):
    return fuzz.ratio(street1.lower(), street2.lower()) >= threshold

# Normalize street names by removing unwanted characters and extra spaces
def normalize_address(address):
    address = address.lower().strip()  # Convert to lowercase and remove leading/trailing spaces
    address = re.sub(r'[^\w\s]', '', address)  # Remove punctuation
    return address

In [29]:
# List to store results as a GeoDataFrame
results = []

# Loop through each point in not_matched_sonden and check for addresses within 200m radius
for index, point_row in not_processed_adress_sonden_match.iterrows():
    center_point = point_row['geometry']  # Get the point from gdf_points
    center_address = point_row['final_address']  # Get the address from gdf_points
    center_id = point_row['GBS_ID']  # Get the ID from gdf_points
    standort = point_row['STANDORT']  # Get the standort from gdf_points
    center_street, center_number = extract_street_and_number(center_address)  # Split address into street and number
    normalized_center_street = normalize_address(center_street)  # Normalize the street name
    buffer = center_point.buffer(500)  # Create a 200m buffer around the point
    
    # Find the addresses from adressen that fall within the buffer
    points_within_radius = adressen[adressen.geometry.within(buffer)]
    
    # Compare the addresses in gdf_addresses to the center_address for digit match and fuzzy match
    matching_addresses = points_within_radius[points_within_radius['ADRESSE_conc'].apply(
        lambda x: (
            check_digit_match(x, center_address) and  # Only proceed if digits match exactly
            is_high_fuzzy_match(
                extract_street_and_number(x)[0], normalized_center_street  # Fuzzy match only if digits match
            )
        )
    )]
    
    # Add matching addresses to results, along with the center_point
    for _, matching_row in matching_addresses.iterrows():
        results.append({
            'Sonden Adresse': center_address,
            'STANDORT': standort,
            'GBS_ID': center_id,
            'ADRESSE': matching_row['ADRESSE'],
            'Adresse_conc': matching_row['ADRESSE_conc'],
            'geometry': matching_row['geometry'],
            'GWR_EGID': matching_row['GWR_EGID']
        })

# Convert the results into a GeoDataFrame
fuzzy_matched = gpd.GeoDataFrame(results, crs=2056)

In [30]:
#solve the bahnhofstrassenproblem again

# Initialize a list to store indices of rows to delete
to_delete = []  

# Record the initial number of entries in `adressen_sonden`
initial_count = len(fuzzy_matched)

# Loop through `sonden` and check the distance condition
for idx, sonden in mastersonden.iterrows():
    # Find the matching entry in `fuzzy_matched` by GBS_ID
    matching_sonde = fuzzy_matched[fuzzy_matched['GBS_ID'] == sonden['GBS_ID']]
    
    if not matching_sonde.empty:
        # Calculate the distance in meters
        distance = sonden.geometry.distance(matching_sonde.geometry.iloc[0])
        print(f"GBS_ID {sonden['GBS_ID']}: Distance = {distance:.2f} meters")

        # Write the calculated distance into the fuzzy_matched dataframe
        fuzzy_matched.loc[matching_sonde.index[0], 'DISTANCE'] = distance
        
        # Check if the distance is greater than 1 km
        if distance > 1000:
            # If the distance is greater than 1 km, flag for deletion
            print(f"GBS_ID {sonden['GBS_ID']}: Failed (Distance > 1 km), marking for deletion.")
            to_delete.append(matching_sonde.index[0])  # Store the index to delete

# Delete the flagged rows from `fuzzy_matched`
fuzzy_matched = fuzzy_matched.drop(to_delete)

# Record the final number of entries in `fuzzy_matched` after deletion
final_count = len(fuzzy_matched)

# Calculate how many entries were deleted
deleted_count = initial_count - final_count

# Print the results
print(f"Remaining entries in fuzzy_matched: {final_count}")
print(f"Entries deleted: {deleted_count}")

GBS_ID m 00-01428: Distance = 11.64 meters
GBS_ID m 00-10842: Distance = 10.28 meters
GBS_ID c 00-10541: Distance = 362.46 meters
GBS_ID n 00-10094: Distance = 6.44 meters
GBS_ID c 00-11315: Distance = 16.12 meters
GBS_ID n 00-10138: Distance = 3.57 meters
GBS_ID m 00-12051: Distance = 9.07 meters
GBS_ID c 00-12621: Distance = 67.17 meters
GBS_ID c 00-10470: Distance = 450.89 meters
GBS_ID c 00-12441: Distance = 25.46 meters
GBS_ID c 00-11743: Distance = 12.10 meters
GBS_ID c 00-10548: Distance = 4.19 meters
GBS_ID c 00-10546: Distance = 6.05 meters
GBS_ID b 01-10123: Distance = 12.78 meters
GBS_ID c 00-11263: Distance = 6.40 meters
GBS_ID b 00-11262: Distance = 17.08 meters
GBS_ID m 00-01460: Distance = 234.99 meters
GBS_ID b 00-10223: Distance = 7.66 meters
GBS_ID b 00-10086: Distance = 56.61 meters
GBS_ID m 00-01404: Distance = 3.31 meters
GBS_ID b 00-10865: Distance = 16.88 meters
GBS_ID l 00-10487: Distance = 8.33 meters
GBS_ID c 00-11951: Distance = 12.94 meters
GBS_ID c 00-12428

In [31]:
# define variante
fuzzy_matched['VARIANTE'] = 'Procesed Fuzzy match'

output = gpd.GeoDataFrame(pd.concat([output, fuzzy_matched[["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "DISTANCE", "VARIANTE", "geometry"]]], ignore_index=True))

not_fuzzy_matched = not_processed_adress_sonden_match[~not_processed_adress_sonden_match['GBS_ID'].isin(output['GBS_ID'])]

In [32]:
def remove_brackets(address):
    # Remove everything from the first '(' (including '(') till the end of the string
    return re.sub(r'\(.*$', '', address).strip()

def split_weird_address_range(address):
    # Pattern to capture:
    # - street name (group 1)
    # - start number (digits) (group 2)
    # - start letter (optional) (group 3)
    # - end number (digits) (group 4)
    # - end letter (optional) (group 5)
    # Separators can be "bis" or "-"
    pattern = re.compile(
        r'^(.*\D)\s*(\d+)([a-zA-Z]?)\s*(?:bis|-)\s*(\d+)([a-zA-Z]?)$', 
        re.IGNORECASE
    )
    m = pattern.match(address.strip())
    
    if not m:
        # no match, return original address in a list
        return [address.strip()]
    
    street = m.group(1).strip()
    start_num = m.group(2)
    start_letter = m.group(3).lower() if m.group(3) else ''
    end_num = m.group(4)
    end_letter = m.group(5).lower() if m.group(5) else ''
    
    # If numbers differ, just return both full addresses
    if start_num != end_num:
        start_addr = f"{street} {start_num}{start_letter}"
        end_addr = f"{street} {end_num}{end_letter}"
        return [start_addr.strip(), end_addr.strip()]
    
    # Numbers are the same — expand letters range if possible
    if start_letter and end_letter:
        letters = list(string.ascii_lowercase)
        try:
            start_index = letters.index(start_letter)
            end_index = letters.index(end_letter)
        except ValueError:
            # If letters not found in a-z, fallback to just both ends
            return [f"{street} {start_num}{start_letter}", f"{street} {end_num}{end_letter}"]
        
        if start_index > end_index:
            # invalid range (e.g., d to a) — fallback to both ends
            return [f"{street} {start_num}{start_letter}", f"{street} {end_num}{end_letter}"]
        
        results = []
        for i in range(start_index, end_index + 1):
            results.append(f"{street} {start_num}{letters[i]}")
        return results
    
    # If no letters or only one letter (can't expand), just return both ends
    start_addr = f"{street} {start_num}{start_letter}"
    end_addr = f"{street} {end_num}{end_letter}"
    return [start_addr.strip(), end_addr.strip()]


In [33]:
not_fuzzy_matched['final_address_2'] = not_fuzzy_matched['final_address'].apply(remove_brackets)

not_fuzzy_matched['final_address_3'] = not_fuzzy_matched['final_address_2'].apply(split_weird_address_range)

not_fuzzy_matched_exploded = not_fuzzy_matched.explode('final_address_3').reset_index(drop=True)

c:\Users\BAA1964\AppData\Local\ESRI\conda\envs\scratch\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
c:\Users\BAA1964\AppData\Local\ESRI\conda\envs\scratch\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [34]:
def remove_haus_after_number(address):
    # Regex explanation:
    #   (.*?\d+[a-zA-Z]?)  -> anything up to (and including) a number + optional letter (non-greedy)
    #   haus.*             -> 'haus' and everything after it
    # Replace full match with just the part before 'haus'
    pattern = re.compile(r'(.*?\d+[a-zA-Z]?)(haus.*)', re.IGNORECASE)
    match = pattern.match(address)
    if match:
        return match.group(1).strip()
    return address.strip()

not_fuzzy_matched_exploded['final_address_4'] = not_fuzzy_matched_exploded['final_address_3'].apply(remove_haus_after_number)

In [35]:
# List to store results as a GeoDataFrame
results = []

# Loop through each point in not_matched_sonden and check for addresses within 200m radius
for index, point_row in not_fuzzy_matched_exploded.iterrows():
    center_point = point_row['geometry']  # Get the point from gdf_points
    center_address = point_row['final_address_4']  # Get the address from gdf_points
    center_id = point_row['GBS_ID']  # Get the ID from gdf_points
    standort = point_row['STANDORT']  # Get the standort from gdf_points
    center_street, center_number = extract_street_and_number(center_address)  # Split address into street and number
    normalized_center_street = normalize_address(center_street)  # Normalize the street name
    buffer = center_point.buffer(500)  # Create a 200m buffer around the point
    
    # Find the addresses from adressen that fall within the buffer
    points_within_radius = adressen[adressen.geometry.within(buffer)]
    
    # Compare the addresses in gdf_addresses to the center_address for digit match and fuzzy match
    matching_addresses = points_within_radius[points_within_radius['ADRESSE_conc'].apply(
        lambda x: (
            check_digit_match(x, center_address) and  # Only proceed if digits match exactly
            is_high_fuzzy_match(
                extract_street_and_number(x)[0], normalized_center_street  # Fuzzy match only if digits match
            )
        )
    )]
    
    # Add matching addresses to results, along with the center_point
    for _, matching_row in matching_addresses.iterrows():
        results.append({
            'Sonden Adresse': center_address,
            'STANDORT': standort,
            'GBS_ID': center_id,
            'ADRESSE': matching_row['ADRESSE'],
            'Adresse_conc': matching_row['ADRESSE_conc'],
            'geometry': matching_row['geometry'],
            'GWR_EGID': matching_row['GWR_EGID']
        })

# Convert the results into a GeoDataFrame
fuzzy_matched_final = gpd.GeoDataFrame(results, crs=2056)

In [36]:
#solve the bahnhofstrassenproblem again

# Initialize a list to store indices of rows to delete
to_delete = []  

# Record the initial number of entries in `adressen_sonden`
initial_count = len(fuzzy_matched_final)

# Loop through `sonden` and check the distance condition
for idx, sonden in mastersonden.iterrows():
    # Find the matching entry in `fuzzy_matched_final` by GBS_ID
    matching_sonde = fuzzy_matched_final[fuzzy_matched_final['GBS_ID'] == sonden['GBS_ID']]
    
    if not matching_sonde.empty:
        # Calculate the distance in meters
        distance = sonden.geometry.distance(matching_sonde.geometry.iloc[0])
        print(f"GBS_ID {sonden['GBS_ID']}: Distance = {distance:.2f} meters")

        # Write the calculated distance into the fuzzy_matched_final dataframe
        fuzzy_matched_final.loc[matching_sonde.index[0], 'DISTANCE'] = distance
        
        # Check if the distance is greater than 1 km
        if distance > 1000:
            # If the distance is greater than 1 km, flag for deletion
            print(f"GBS_ID {sonden['GBS_ID']}: Failed (Distance > 1 km), marking for deletion.")
            to_delete.append(matching_sonde.index[0])  # Store the index to delete

# Delete the flagged rows from `fuzzy_matched_final`
fuzzy_matched_final = fuzzy_matched_final.drop(to_delete)

# Record the final number of entries in `fuzzy_matched_final` after deletion
final_count = len(fuzzy_matched_final)

# Calculate how many entries were deleted
deleted_count = initial_count - final_count

# Print the results
print(f"Remaining entries in fuzzy_matched_final: {final_count}")
print(f"Entries deleted: {deleted_count}")

GBS_ID n 00-10647: Distance = 5.37 meters
GBS_ID b 00-10681: Distance = 12.01 meters
GBS_ID d 00-12497: Distance = 4.82 meters
GBS_ID l 00-11508: Distance = 8.61 meters
GBS_ID l 00-11035: Distance = 67.34 meters
GBS_ID e 00-13289: Distance = 76.24 meters
GBS_ID d 00-10894: Distance = 28.62 meters
GBS_ID g 00-10671: Distance = 68.86 meters
GBS_ID f 08-10026: Distance = 45.98 meters
GBS_ID h 00-11770: Distance = 7.37 meters
GBS_ID h 00-11773: Distance = 5.01 meters
GBS_ID c 00-11307: Distance = 405.61 meters
GBS_ID c 00-11377: Distance = 49.92 meters
GBS_ID n 00-11178: Distance = 8.07 meters
GBS_ID m 00-11979: Distance = 22.77 meters
GBS_ID c 00-11741: Distance = 9.01 meters
GBS_ID c 00-12069: Distance = 8.50 meters
GBS_ID m 00-11053: Distance = 19.06 meters
GBS_ID m 00-10827: Distance = 4.09 meters
GBS_ID m 00-01155: Distance = 5.32 meters
GBS_ID b 00-12548: Distance = 5.64 meters
GBS_ID d 00-12590: Distance = 40.02 meters
GBS_ID g 00-10497: Distance = 32.99 meters
GBS_ID l 00-11643: Di

In [37]:
# define variante
fuzzy_matched_final['VARIANTE'] = 'Procesed Fuzzy match final'

output = gpd.GeoDataFrame(pd.concat([output, fuzzy_matched_final[["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "DISTANCE", "VARIANTE", "geometry"]]], ignore_index=True))

last_resort = mastersonden[~mastersonden['GBS_ID'].isin(output['GBS_ID'])]    

In [38]:
proj_gebäude['Projektiert'] = 'JA'
gebäude['Projektiert'] = 'Nein'


all_gebäude =  gpd.GeoDataFrame(pd.concat([proj_gebäude, gebäude], ignore_index=True))

all_gebäude_centroids = all_gebäude.copy()

all_gebäude_centroids['geometry'] = all_gebäude.geometry.centroid

all_gebäude_liegenschaften = all_gebäude_centroids.sjoin(liegeschaften, how="left", predicate="within")

adressen_filtered = adressen[adressen['GWR_EGID'].notna()]

all_gebäude_adressen_liegenschaften = all_gebäude_liegenschaften.merge(
    adressen_filtered[['GWR_EGID', 'ADRESSE']],
    on='GWR_EGID',
    how='left'
)

sonden_liegenschaften = last_resort.sjoin(liegeschaften, how="left", predicate="intersects")



In [39]:
def filter_out_number_dot_number(address):
    # Ensure it's a string before applying regex
    address = str(address)
    return not re.search(r'(?:\d+)?\.\d', address)
    
    
all_gebäude_adressen_liegenschaften = all_gebäude_adressen_liegenschaften[all_gebäude_adressen_liegenschaften['ADRESSE'].apply(filter_out_number_dot_number)]

In [40]:


matched_pairs = []

# Loop over each shared region
for region in sonden_liegenschaften['EGRIS_EGRID'].unique():
    sonden_subset = sonden_liegenschaften[sonden_liegenschaften['EGRIS_EGRID'] == region].copy().reset_index(drop=True)
    gebaeude_subset = all_gebäude_adressen_liegenschaften[all_gebäude_adressen_liegenschaften['EGRIS_EGRID'] == region].copy().reset_index(drop=True)
    
    # Keep looping while both have rows
    while not sonden_subset.empty and not gebaeude_subset.empty:
        min_distance = float('inf')
        best_sonde_pos = None
        best_gebaeude_pos = None

        for s_idx, sonde in sonden_subset.iterrows():
            distances = gebaeude_subset.geometry.distance(sonde.geometry)
            g_idx = distances.idxmin()
            g_pos = gebaeude_subset.index.get_loc(g_idx)  # Get positional index
            dist = distances[g_idx]
            if dist < min_distance:
                min_distance = dist
                best_sonde_pos = s_idx
                best_gebaeude_pos = g_pos

        # Record the match
        matched_pairs.append({
            'GBS_ID': sonden_subset.iloc[best_sonde_pos]['GBS_ID'],
            'GWR_EGID': gebaeude_subset.iloc[best_gebaeude_pos]['GWR_EGID'],
            'DISTANCE': min_distance,
            'EGRIS_EGRID': region,
            "STANDORT" : sonden_subset.iloc[best_sonde_pos]['STANDORT'],
            "ADRESSE": gebaeude_subset.iloc[best_gebaeude_pos]['ADRESSE'],
            "ARTZH": gebaeude_subset.iloc[best_gebaeude_pos]['ARTZH'],
            "geometry": gebaeude_subset.iloc[best_gebaeude_pos]['geometry']
        })

        # Remove matched rows and reset index
        sonden_subset = sonden_subset.drop(index=best_sonde_pos).reset_index(drop=True)
        gebaeude_subset = gebaeude_subset.drop(index=best_gebaeude_pos).reset_index(drop=True)

nearest_gebäude = gpd.GeoDataFrame(matched_pairs, geometry='geometry', crs=sonden_liegenschaften.crs)


In [41]:
nearest_gebäude['VARIANTE'] = "Nächstes Gebäude"
output = gpd.GeoDataFrame(pd.concat([output, nearest_gebäude[["STANDORT", "ADRESSE", "GBS_ID", "GWR_EGID", "DISTANCE", "VARIANTE", "geometry"]]], ignore_index=True))


In [42]:
output = gpd.GeoDataFrame(pd.concat([output, output_spatial], ignore_index=True))


In [43]:
output.to_csv("output.csv")

In [44]:
import datetime

today = datetime.date.today()

not_matched_at_all = mastersonden[~mastersonden['GBS_ID'].isin(output['GBS_ID'])]

not_matched_at_all.to_excel(f"not_matched_{today}.xlsx")

In [45]:
output['GWR_EGID'] = output['GWR_EGID'].fillna(0).astype(int)
output.to_excel(f"output_{today}.xlsx")

In [46]:
output.to_excel(f"output_{today}.xlsx")

In [47]:
not_matched_at_all

GBS_ID                                           STANDORT  \
205    c 00-12589                          Kellerrainstrasse, Haus A   
287    m 00-11952                                  Badenerstrasse 13   
572    m 00-11292                            Buechenstrasse, Haus 10   
573    m 00-11299                            Buechenstrasse, Haus 17   
795    c 00-10561                              Im Weieracher Haus G2   
...           ...                                                ...   
33280  l 00-11704                                    Chröpflistrasse   
33312  b 23-10013                                        Wattstrasse   
34086  e 00-12565                               Langackerstrasse 133   
36088  f 00-12536  Arealüberbauung mit 8 MFH,\r\nBergblickstrasse...   
36113  f 00-12327                                      Neuhusstrasse   

                              geometry  
205    POINT (2674108.828 1235128.877)  
287    POINT (2675110.994 1256817.951)  
572    POINT (2677237.051 1264984.993)  
573    POINT (2677282.051 1265019.993)  
795    POINT (2679189.844 1235567.838)  
...                                ...  
33280   POINT (2683425.09 1264610.953)  
33312  POINT (2683539.924 1251900.845)  
34086   POINT (2689009.04 1238285.946)  
36088  POINT (2706375.818 1234915.777)  
36113  POINT (2706495.813 1234401.775)  

[142 rows x 3 columns]

In [48]:
old1 = pd.read_excel(r"C:\dev\ews\26.6\output_2025-06-26.xlsx")
old2 = pd.read_excel(r"C:\dev\ews\26.6\output_2025-07-14.xlsx")

old_all = pd.concat([old1,old2])

In [49]:
len(old_all)

53902

In [53]:
len(output)

53389

In [54]:
is_not_in_new = old_all[~old_all['GBS_ID'].isin(output['GBS_ID'])]


In [55]:
is_not_in_new

STANDORT                 ADRESSE      GBS_ID  \
33970            Risigrundstrasse  Risigrundstrasse 14b.1  n 00-10247   
34110          Uerzlikerstrasse 2   Uerzlikerstrasse 2b.1  c 00-11338   
34159             Bergmattstrasse   Bergmattstrasse 21a.1  c 00-10490   
37830          Grosszelgstrasse 6   Grosszelgstrasse 6a.1  l 00-11292   
56                 Büelstrasse 3b          Büelstrasse 3b  c 00-10561   
59                   Bitziberg 24            Bitziberg 24  l 00-10310   
60                   Bitziberg 24            Bitziberg 24  l 00-10312   
158                Büelstrasse 7b          Büelstrasse 7b  c 00-10556   
181               Itziker-Str. 23         Itziker-Str. 23  f 00-11572   
238                    Brünggen 3              Brünggen 3  h 00-10119   
296               Itziker-Str. 25         Itziker-Str. 25  f 00-11571   
376           Weinbergstrasse 14a     Weinbergstrasse 14a  m 00-10455   
379              Schwenkelberg 77        Schwenkelberg 77  m 00-10326   
415        Hasenbühlstrasse 18i-m    Hasenbühlstrasse 18k  c 00-01288   
475        Hasenbühlstrasse 18i-m    Hasenbühlstrasse 18m  c 00-01288   
504    Im Tobelacker 10, 10a, 10b       Im Tobelacker 10b  g 00-10287   
505    Im Tobelacker 10, 10a, 10b        Im Tobelacker 10  g 00-10287   
551        Hasenbühlstrasse 18i-m    Hasenbühlstrasse 18i  c 00-01288   
573    Im Tobelacker 10, 10a, 10b       Im Tobelacker 10a  g 00-10287   
822        Hasenbühlstrasse 18i-m    Hasenbühlstrasse 18l  c 00-01288   

        GWR_EGID   DISTANCE                 VARIANTE  \
33970  210288197   7.038548         Nächstes Gebäude   
34110  210229087   4.897739         Nächstes Gebäude   
34159  210241864   4.249286         Nächstes Gebäude   
37830  192065050  32.642249         Nächstes Gebäude   
56     201029119   3.564465       Single Adress Join   
59     201025337  26.706188       Single Adress Join   
60     201025337  30.130922       Single Adress Join   
158    201029123  18.247893       Single Adress Join   
181    210219534  24.279795       Single Adress Join   
238    200294746  19.325834       Single Adress Join   
296    210219533  16.446911       Single Adress Join   
376    201005078  11.838766       Single Adress Join   
379    201008108  14.996454       Single Adress Join   
415      3022305  20.373202  Processed Adressen join   
475      3022307  26.057448  Processed Adressen join   
504    201040636  50.848774  Processed Adressen join   
505    201040640  22.498548  Processed Adressen join   
551      3022304  19.988552  Processed Adressen join   
573    201040635  18.028967  Processed Adressen join   
822      3022306  24.352763  Processed Adressen join   

                                            geometry  Unnamed: 0  
33970     POINT (2676386.0016504 1245668.8707199797)         NaN  
34110   POINT (2680022.4870989127 1231572.714916546)         NaN  
34159  POINT (2682969.5855192547 1233168.1484290715)         NaN  
37830   POINT (2687780.775999999 1258739.0485000017)         NaN  
56     POINT (2679188.5040000007 1235564.5349999964)        56.0  
59     POINT (2683417.2569999993 1261569.1550000012)        59.0  
60     POINT (2683417.2569999993 1261569.1550000012)        60.0  
158             POINT (2679227.8830000013 1235525.5)       158.0  
181     POINT (2700081.348000001 1237299.2239999995)       181.0  
238    POINT (2699943.5309999995 1256193.5300000012)       238.0  
296           POINT (2700068.443 1237334.7129999995)       296.0  
376    POINT (2675261.8759999983 1256992.0160000026)       376.0  
379                  POINT (2677042.068 1256622.136)       379.0  
415    POINT (2676729.9580000006 1236105.9069999978)       415.0  
475    POINT (2676734.2600000016 1236093.8290000036)       475.0  
504     POINT (2688258.811999999 1247980.4310000017)       504.0  
505    POINT (2688229.4750000015 1248043.2440000027)       505.0  
551     POINT (2676728.993999999 1236108.4839999974)       551.0  
573     POINT (2688242.572999999 1248010.

In [ ]:
output